# Composição Temporal
- Teste para agrupamento de imagens por intervalo temporal
- Este notebook irá demonstrar como agrupar as imagens coletadas por mês

In [30]:
import ee
import geemap
import sys
import os
from datetime import datetime
sys.path.append(os.path.abspath(os.path.join(os.getcwd(),os.pardir)))
from src import eetools as eet

In [2]:
try: 
    ee.Initialize()
except:
    ee.Authenticate()
    ee.Initialize()


Successfully saved authorization token.


In [34]:
coordenadas = "-48.53801472648439,-22.503806214013736,-48.270222978437516,-22.7281869567509"
x1, y1, x2, y2 = coordenadas.split(",")

datas = "2013-01-01,2023-12-31"
inicio, fim = datas.split(",")
escala = 30

geom = ee.Geometry.Polygon([[[float(x1),float(y2)],
                             [float(x2),float(y2)],
                             [float(x2),float(y1)],
                             [float(x1),float(y1)],
                             [float(x1),float(y2)]]])

latitude_central = (float(x1)+float(x2))/2
longitude_central = (float(y1)+float(y2))/2

In [35]:
collec = ee.ImageCollection('LANDSAT/LC08/C01/T1_SR')\
    .filterBounds(geom)\
    .filterDate(inicio,fim)\
    .filterMetadata('CLOUD_COVER','less_than',30)

In [54]:
collec_ndvi = collec.map(eet.ndvi)
collec_ndvi

In [90]:
years = ee.List.sequence(
    datetime.strptime(inicio, '%Y-%m-%d').year,
    datetime.strptime(fim, '%Y-%m-%d').year
)
years

In [91]:
composite = ee.ImageCollection(
    years.map(
        lambda y: collec_ndvi\
            .filter(ee.Filter.calendarRange(y,y,'year'))\
            .median()\
            .set("year",y,"system:id",y)\
            .set("system:index",ee.Number(y).format("%04d"))
    )
)\
    .map(lambda image: image.set('num_bands', image.bandNames().size()))\
    .filter('num_bands != 0')

composite

In [92]:
time_series = composite.select('ndvi').toBands()
time_series

In [93]:
Map = geemap.Map(center = (longitude_central, latitude_central), zoom=10, basemap = 'HYBRID')

vis_params = {
    'min':-1,
    'max': 1,
    'palette': ['#a50026','#d73027','#f46d43','#fdae61','#fee08b','#ffffbf','#d9ef8b','#a6d96a','#66bd63','#1a9850','#006837']
}
Map.addLayer(time_series.select('2021_ndvi'), vis_params, 'NDVI')

Map

Map(center=[-22.61599658538232, -48.404118852460954], controls=(WidgetControl(options=['position', 'transparen…

In [24]:
composite.select('ndvi').toBands()

In [103]:
def median_by_year(image_collection, year_start, year_end):
    years = ee.List.sequence(year_start, year_end)

    composite = ee.ImageCollection(
        years.map(
            lambda y: image_collection\
                .filter(ee.Filter.calendarRange(y,y,'year'))\
                .median()\
                .set("year",y,"system:id",y)\
                .set("system:index",ee.Number(y).format("%04d"))
        )
    )\
        .map(lambda image: image.set('num_bands', image.bandNames().size()))\
        .filter('num_bands != 0')

    return composite

median_by_year(collec_ndvi,2011,2024)